In [1]:
import os, csv, json, time, random, requests
import folium
from folium.plugins import MarkerCluster
from IPython.display import display
from datetime import date, timedelta


def afficher_carte(carte_folium):
    display(carte_folium)


class MeteoClients:
    BASE_URL = "https://api.open-meteo.com/v1/forecast"

    def __init__(self, timeout=15, timezone="Europe/Paris"):
        self.timeout = timeout
        self.timezone = timezone

    def get_meteo_actuelle(self, lat, lon):
        params = {
            "latitude": lat,
            "longitude": lon,
            "current": "temperature_2m,precipitation,wind_speed_10m,weather_code",
            "timezone": self.timezone
        }
        r = requests.get(self.BASE_URL, params=params, timeout=self.timeout)
        r.raise_for_status()
        cur = (r.json().get("current") or {})
        return {
            "time": cur.get("time"),
            "temperature_c": cur.get("temperature_2m"),
            "pluie_mm": cur.get("precipitation"),
            "vent_kmh": cur.get("wind_speed_10m"),
            "weather_code": cur.get("weather_code"),
        }

    @staticmethod
    def resume(m):
        if not m:
            return "N/A"
        return (
            f"{m.get('time')} | {m.get('temperature_c')}°C | "
            f"pluie {m.get('pluie_mm')} mm | vent {m.get('vent_kmh')} km/h"
        )


class RouteClients:
    ORS_BASE = "https://api.openrouteservice.org"

    API_KEY = "eyJvcmciOiI1YjNjZTM1OTc4NTExMTAwMDFjZjYyNDgiLCJpZCI6IjczZjJkYzk5YjNhMTRhZTk5ZTQzMDNkZTAzODE5ZTBmIiwiaCI6Im11cm11cjY0In0="

    PROFILS = {
        "1": ("Voiture", "driving-car"),
        "2": ("Vélo", "cycling-regular"),
        "3": ("Marche", "foot-walking")
    }

    # estimation voiture (moyennes)
    PRIX_CARBURANT_EUR_L = 1.75
    CONSO_MOY_L_100KM = 6.0
    PEAGE_EUR_100KM = 9.5
    PEAGE_EUR_KM = PEAGE_EUR_100KM / 100.0

    def __init__(self, timeout=20, cache_dir="cache_routes"):
        self.timeout = timeout
        self.cache_dir = cache_dir
        os.makedirs(self.cache_dir, exist_ok=True)

    def _get(self, url, params=None):
        headers = {"Authorization": self.API_KEY}
        r = requests.get(url, headers=headers, params=params or {}, timeout=self.timeout)
        if r.status_code != 200:
            raise RuntimeError(f"ORS GET {r.status_code}: {r.text[:250]}")
        return r.json()

    def _post(self, url, body=None):
        headers = {"Authorization": self.API_KEY, "Content-Type": "application/json"}
        r = requests.post(url, headers=headers, json=body or {}, timeout=self.timeout)
        if r.status_code != 200:
            raise RuntimeError(f"ORS POST {r.status_code}: {r.text[:250]}")
        return r.json()

    def _cache_path(self, prefix, key):
        safe = "".join(
            c for c in key.lower()
            if c.isalnum() or c in ("_", "-", ".", "[", "]", ",", " ")
        )
        return os.path.join(self.cache_dir, f"{prefix}_{safe}.json")

    def _cache_load(self, prefix, key, max_age_seconds=7 * 24 * 3600):
        path = self._cache_path(prefix, key)
        if not os.path.exists(path):
            return None
        if (time.time() - os.path.getmtime(path)) > max_age_seconds:
            return None
        try:
            with open(path, "r", encoding="utf-8") as f:
                return json.load(f)
        except Exception:
            return None

    def _cache_save(self, prefix, key, data):
        path = self._cache_path(prefix, key)
        with open(path, "w", encoding="utf-8") as f:
            json.dump(data, f, ensure_ascii=False, indent=2)

    def geocoder_ville(self, ville, country="FR"):
        cache_key = f"{ville}_{country}"
        cached = self._cache_load("geocode", cache_key)
        if cached:
            return cached["coords"], cached.get("label", ville)

        url = f"{self.ORS_BASE}/geocode/search"
        params = {"text": ville, "boundary.country": country, "size": 1}
        data = self._get(url, params=params)

        feats = data.get("features", [])
        if not feats:
            raise ValueError(f"Aucun résultat ORS geocoding pour : {ville}")

        best = feats[0]
        coords = best["geometry"]["coordinates"]  # [lon, lat]
        label = (best.get("properties") or {}).get("label", ville)

        self._cache_save("geocode", cache_key, {"coords": coords, "label": label})
        return coords, label

    def calculer_itineraire(self, coords_from, coords_to, profil):
        cache_key = f"{profil}_{coords_from}_{coords_to}"
        cached = self._cache_load("route", cache_key)
        if cached:
            return cached

        url = f"{self.ORS_BASE}/v2/directions/{profil}/geojson"
        body = {"coordinates": [coords_from, coords_to]}
        data = self._post(url, body=body)

        self._cache_save("route", cache_key, data)
        return data

    @staticmethod
    def extraire_distance_duree(route_geojson):
        feats = route_geojson.get("features", [])
        if not feats:
            return None, None
        summary = ((feats[0].get("properties") or {}).get("summary") or {})
        return summary.get("distance"), summary.get("duration")

    @staticmethod
    def format_duree(duration_s):
        if duration_s is None:
            return "N/A"
        minutes = int(round(duration_s / 60))
        h, m = minutes // 60, minutes % 60
        return f"{h}h{m:02d}" if h else f"{m} min"

    def estimer_prix_voiture(self, distance_m):
        if distance_m is None:
            return None
        km = distance_m / 1000.0
        litres = (km / 100.0) * self.CONSO_MOY_L_100KM
        carburant = litres * self.PRIX_CARBURANT_EUR_L
        peage = km * self.PEAGE_EUR_KM
        return {
            "distance_km": round(km, 1),
            "litres": round(litres, 2),
            "carburant_eur": round(carburant, 2),
            "peage_eur": round(peage, 2),
            "total_eur": round(carburant + peage, 2),
        }


class POILoader:
    def __init__(self, dossier_csv="."):
        self.dossier_csv = dossier_csv

    @staticmethod
    def _to_float(v):
        try:
            return float(v) if v not in (None, "") else None
        except Exception:
            return None

    def _read(self, path):
        if not os.path.exists(path):
            return []
        with open(path, "r", encoding="utf-8-sig", newline="") as f:
            return list(csv.DictReader(f, delimiter=";"))

    def load_destination(self, ville):
        v = ville.lower()
        hotels = self._read(os.path.join(self.dossier_csv, f"hotels_{v}.csv"))
        restos = self._read(os.path.join(self.dossier_csv, f"restaurants_{v}.csv"))
        lieux = self._read(os.path.join(self.dossier_csv, f"lieux_historiques_{v}.csv"))

        for arr in (hotels, restos, lieux):
            for r in arr:
                r["latitude"] = self._to_float(r.get("latitude"))
                r["longitude"] = self._to_float(r.get("longitude"))
        return hotels, restos, lieux

    @staticmethod
    def centre_moyen(lignes, fallback=(50.6292, 3.0573)):
        lats, lons = [], []
        for r in lignes:
            if r.get("latitude") is not None and r.get("longitude") is not None:
                lats.append(r["latitude"])
                lons.append(r["longitude"])
        if not lats:
            return fallback
        return sum(lats) / len(lats), sum(lons) / len(lons)


class MapBuilder:
    @staticmethod
    def _popup_nom(nom):
        return folium.Popup(nom or "Sans nom", max_width=250)

    def carte_poi(self, titre, lignes, centre):
        m = folium.Map(location=centre, zoom_start=13)
        cl = MarkerCluster(name=titre).add_to(m)

        for r in lignes:
            lat, lon = r.get("latitude"), r.get("longitude")
            if lat is None or lon is None:
                continue
            folium.Marker(
                [lat, lon],
                tooltip=r.get("nom") or titre,
                popup=self._popup_nom(r.get("nom"))
            ).add_to(cl)

        folium.LayerControl().add_to(m)
        return m

    def carte_route(self, route_geojson, center):
        m = folium.Map(location=center, zoom_start=7)
        fg = folium.FeatureGroup(name="Trajet", show=True)
        folium.GeoJson(route_geojson, tooltip="Trajet").add_to(fg)
        fg.add_to(m)
        folium.LayerControl().add_to(m)
        return m

    def carte_globale(self, centre, hotels, restos, lieux, route_geojson):
        m = folium.Map(location=centre, zoom_start=13)

        fg_h = folium.FeatureGroup(name="Hôtels", show=True)
        fg_r = folium.FeatureGroup(name="Restaurants", show=False)
        fg_l = folium.FeatureGroup(name="Lieux historiques", show=False)

        cl_h = MarkerCluster().add_to(fg_h)
        cl_r = MarkerCluster().add_to(fg_r)
        cl_l = MarkerCluster().add_to(fg_l)

        for r in hotels:
            if r.get("latitude") is None or r.get("longitude") is None:
                continue
            folium.Marker(
                [r["latitude"], r["longitude"]],
                tooltip=r.get("nom") or "Hôtel",
                popup=self._popup_nom(r.get("nom"))
            ).add_to(cl_h)

        for r in restos:
            if r.get("latitude") is None or r.get("longitude") is None:
                continue
            folium.Marker(
                [r["latitude"], r["longitude"]],
                tooltip=r.get("nom") or "Restaurant",
                popup=self._popup_nom(r.get("nom"))
            ).add_to(cl_r)

        for r in lieux:
            if r.get("latitude") is None or r.get("longitude") is None:
                continue
            folium.Marker(
                [r["latitude"], r["longitude"]],
                tooltip=r.get("nom") or "Lieu",
                popup=self._popup_nom(r.get("nom"))
            ).add_to(cl_l)

        fg_h.add_to(m)
        fg_r.add_to(m)
        fg_l.add_to(m)

        fg_route = folium.FeatureGroup(name="Trajet", show=True)
        folium.GeoJson(route_geojson, tooltip="Trajet").add_to(fg_route)
        fg_route.add_to(m)

        folium.LayerControl(collapsed=False).add_to(m)
        return m

    def carte_selection(self, centre, hotel_unique, restos_selectionnes, lieux_selectionnes):
        m = folium.Map(location=centre, zoom_start=13)

        fg_h = folium.FeatureGroup(name="Hôtel (sélection)", show=True)
        fg_r = folium.FeatureGroup(name="Restaurants (sélection)", show=True)
        fg_l = folium.FeatureGroup(name="Activités (sélection)", show=True)

        if hotel_unique and hotel_unique.get("latitude") is not None and hotel_unique.get("longitude") is not None:
            folium.Marker(
                [hotel_unique["latitude"], hotel_unique["longitude"]],
                tooltip=hotel_unique.get("nom") or "Hôtel",
                popup=self._popup_nom(hotel_unique.get("nom"))
            ).add_to(fg_h)

        cl_r = MarkerCluster().add_to(fg_r)
        for r in restos_selectionnes:
            if r.get("latitude") is None or r.get("longitude") is None:
                continue
            folium.Marker(
                [r["latitude"], r["longitude"]],
                tooltip=r.get("nom") or "Restaurant",
                popup=self._popup_nom(r.get("nom"))
            ).add_to(cl_r)

        cl_l = MarkerCluster().add_to(fg_l)
        for l in lieux_selectionnes:
            if l.get("latitude") is None or l.get("longitude") is None:
                continue
            folium.Marker(
                [l["latitude"], l["longitude"]],
                tooltip=l.get("nom") or "Lieu",
                popup=self._popup_nom(l.get("nom"))
            ).add_to(cl_l)

        fg_h.add_to(m)
        fg_r.add_to(m)
        fg_l.add_to(m)
        folium.LayerControl(collapsed=False).add_to(m)
        return m


class TravelPlanner:
    def choisir_hotel_unique(self, hotels):
        ok = [h for h in hotels if h.get("latitude") is not None and h.get("longitude") is not None]
        return random.choice(ok) if ok else None

    def _pick(self, items, k, used):
        c = [x for x in items if x.get("nom") and x.get("nom") not in used]
        if len(c) <= k:
            return c
        return random.sample(c, k)

    def planifier(self, date_depart, nb_jours, hotels, restos, lieux):
        hotel = self.choisir_hotel_unique(hotels)

        restos_ok = [r for r in restos if r.get("latitude") is not None and r.get("longitude") is not None]
        lieux_ok = [l for l in lieux if l.get("latitude") is not None and l.get("longitude") is not None]

        used_r, used_a = set(), set()
        plan = []

        for i in range(nb_jours):
            d = (date_depart + timedelta(days=i)).isoformat()

            r_day = self._pick(restos_ok, 2, used_r)
            for r in r_day:
                used_r.add(r.get("nom"))

            a_day = self._pick(lieux_ok, 2, used_a)
            for a in a_day:
                used_a.add(a.get("nom"))

            plan.append({
                "jour": i + 1,
                "date": d,
                "restaurants": r_day,
                "activites": a_day
            })

        recap = {
            "hotel": hotel,
            "restaurants_uniques": sorted(list(used_r)),
            "activites_uniques": sorted(list(used_a))
        }
        return plan, recap


Script d'éxecution utilisateur 

In [3]:
ville_depart = input("Ville de départ : ").strip()
ville_arrivee = input("Ville d'arrivée : ").strip()

s = input("Date de départ (YYYY-MM-DD) : ").strip()
y, m, d = [int(x) for x in s.split("-")]
date_depart = date(y, m, d)

duree_jours = int(input("Durée du voyage (en jours) : ").strip())
nb_personnes = int(input("Nombre de personnes : ").strip())

print("Mode : 1) Voiture  2) Vélo  3) Marche")
choix = input("Choix (1/2/3) : ").strip()
if choix not in ("1", "2", "3"):
    choix = "1"
mode_label, profil = RouteClients.PROFILS[choix]

meteo_client = MeteoClients()
route_client = RouteClients()
poi_loader = POILoader(dossier_csv=".")
map_builder = MapBuilder()
planner = TravelPlanner()

# Route (ORS)
coords_from, label_from = route_client.geocoder_ville(ville_depart)
coords_to, label_to = route_client.geocoder_ville(ville_arrivee)

route_geojson = route_client.calculer_itineraire(coords_from, coords_to, profil)
dist_m, dur_s = route_client.extraire_distance_duree(route_geojson)

# Météo actuelle
meteo_depart = meteo_client.get_meteo_actuelle(lat=coords_from[1], lon=coords_from[0])
meteo_arrivee = meteo_client.get_meteo_actuelle(lat=coords_to[1], lon=coords_to[0])

# POI destination (CSV)
hotels, restos, lieux = poi_loader.load_destination(ville_arrivee)
centre_dest = poi_loader.centre_moyen(hotels + restos + lieux, fallback=(coords_to[1], coords_to[0]))

# Planning
plan, recap = planner.planifier(date_depart, duree_jours, hotels, restos, lieux)

# Construire listes “sélectionnées” (objets complets) à partir du planning
restos_selectionnes = []
lieux_selectionnes = []
seen_restos = set()
seen_lieux = set()

for day in plan:
    for r in day["restaurants"]:
        nom = r.get("nom")
        if nom and nom not in seen_restos:
            restos_selectionnes.append(r)
            seen_restos.add(nom)

    for a in day["activites"]:
        nom = a.get("nom")
        if nom and nom not in seen_lieux:
            lieux_selectionnes.append(a)
            seen_lieux.add(nom)

# Résumé trajet
km = dist_m / 1000 if dist_m else None

print("\n--- RÉSUMÉ ---")
print("Départ :", label_from)
print("Arrivée :", label_to)
print("Date départ :", date_depart.isoformat())
print("Durée (jours) :", duree_jours)
print("Personnes :", nb_personnes)
print("Mode de transport :", mode_label, "(", profil, ")")
print("Distance (km) :", round(km, 1) if km else "N/A")
print("Durée route :", route_client.format_duree(dur_s))

# Estimation transport (uniquement voiture)
cout_transport = 0.0
if mode_label == "Voiture":
    prix = route_client.estimer_prix_voiture(dist_m)
    if prix:
        cout_transport = prix["total_eur"]
        print("Transport total :", cout_transport, "€")
        print("Transport par personne :", round(cout_transport / max(nb_personnes, 1), 2),"€")

print("\n--- MÉTÉO ACTUELLE ---")
print("Départ :", MeteoClients.resume(meteo_depart))
print("Arrivée :", MeteoClients.resume(meteo_arrivee))

print("\n--- HÔTEL  ---")
hotel_nom = recap["hotel"].get("nom", "Sans nom") if recap["hotel"] else "Aucun hôtel"
print(hotel_nom)

print("\n--- PLANNING ---")
for day in plan:
    print(f"\nJour {day['jour']}  ({day['date']})")
    print("Restaurants :", [r.get("nom") for r in day["restaurants"] if r.get("nom")])
    print("Activités :", [a.get("nom") for a in day["activites"] if a.get("nom")])

print("\n--- RÉCAP FINAL ---")
print("Hôtel :", hotel_nom)
print("Restaurants proposés :", recap["restaurants_uniques"])
print("Activités proposées :", recap["activites_uniques"])

# Budget estimé (hypothèses moyennes France)
PRIX_MOY_REPAS_EUR = 18.0
PRIX_MOY_NUIT_HOTEL_EUR = 98.49

nb_repas_total = duree_jours * 2 * nb_personnes  # 2 repas/jour/personne
cout_repas = nb_repas_total * PRIX_MOY_REPAS_EUR

# nuits : on prend (jours - 1) au minimum 1 (ex: 1 jour => 1 nuit)
nb_nuits = max(duree_jours - 1, 1)
cout_hotel = nb_nuits * PRIX_MOY_NUIT_HOTEL_EUR

budget_total = cout_transport + cout_repas + cout_hotel
budget_par_personne = budget_total / max(nb_personnes, 1)

print("\n--- NOTE FINALE (PRIX ESTIMÉ) ---")
print("Nombre de repas total :", nb_repas_total, "->", round(cout_repas, 2), "€")
print("Nombre de nuits à l'hôtel :", nb_nuits, "->", round(cout_hotel, 2), "€")
print("Transport :", round(cout_transport, 2), "€")
print("Total :", round(budget_total, 2), "€")
print("Total par personne :", round(budget_par_personne, 2), "€")

print("\n--- CARTES ---")
afficher_carte(map_builder.carte_route(route_geojson, center=centre_dest))
afficher_carte(map_builder.carte_poi("Hôtels", hotels, centre_dest))
afficher_carte(map_builder.carte_poi("Restaurants", restos, centre_dest))
afficher_carte(map_builder.carte_poi("Lieux historiques", lieux, centre_dest))
afficher_carte(map_builder.carte_globale(centre_dest, hotels, restos, lieux, route_geojson))

# Carte finale : uniquement les lieux sélectionnés (hôtel + restos choisis + activités choisies)
afficher_carte(
    map_builder.carte_selection(
        centre=centre_dest,
        hotel_unique=recap["hotel"],
        restos_selectionnes=restos_selectionnes,
        lieux_selectionnes=lieux_selectionnes
    )
)


Ville de départ :  Paris
Ville d'arrivée :  Lille
Date de départ (YYYY-MM-DD) :  2026-01-03
Durée du voyage (en jours) :  4
Nombre de personnes :  2


Mode : 1) Voiture  2) Vélo  3) Marche


Choix (1/2/3) :  1



--- RÉSUMÉ ---
Départ : Paris, France
Arrivée : Lille, France
Date départ : 2026-01-03
Durée (jours) : 4
Personnes : 2
Mode de transport : Voiture ( driving-car )
Distance (km) : 220.4
Durée route : 2h22
Transport total : 44.07 €
Transport par personne : 22.04 €

--- MÉTÉO ACTUELLE ---
Départ : 2026-01-25T20:30 | 6.5°C | pluie 0.0 mm | vent 3.1 km/h
Arrivée : 2026-01-25T20:30 | 4.4°C | pluie 0.0 mm | vent 7.9 km/h

--- HÔTEL  ---
Hôtel Ibis Styles Lille Centre Grand Place

--- PLANNING ---

Jour 1  (2026-01-03)
Restaurants : ['Lety Délices', 'Level Up']
Activités : ['Église de la Trompette', 'Porte de Roubaix']

Jour 2  (2026-01-04)
Restaurants : ['Friterie du Marais', "Café de l'Octroi"]
Activités : ['Palais Rihour', 'Église Saint-Maurice']

Jour 3  (2026-01-05)
Restaurants : ['La Vieille France', 'La Petite Place']
Activités : ['Église du Sacré-Cœur', 'Église Protestante Unie de France']

Jour 4  (2026-01-06)
Restaurants : ["D'wich Home", 'La Guinguette de la Marine']
Activités : ['